In [ ]:
%matplotlib inline

In [12]:
# -*- coding: utf-8 -*-
""" .....................

################################################################################
# Author: Weikun Han <weikunhan@gmail.com>
# Crate Date: 04/07/2018        
# Update:
# Reference: 
#    https://github.com/michalfaber/keras_Realtime_Multi-Person_Pose_Estimation
################################################################################
"""

from pycocotools.coco import COCO
from scipy.spatial.distance import cdist
import numpy as np
import cv2
import os
import os.path
import struct
import h5py

def process():
    count = 0
    for j, ds in enumerate(datasets):

        anno_path = ds[0]
        images_dir = ds[1]
        masks_dir = ds[2]
        dataset_type = ds[3]

        coco = COCO(anno_path)
        ids = list(coco.imgs.keys())
        max_images = len(ids)
        #for i, img_id in enumerate(ids[744:745]):
        for i, img_id in enumerate(ids):
            ann_ids = coco.getAnnIds(imgIds=img_id)
            img_anns = coco.loadAnns(ann_ids)

            numPeople = len(img_anns)
            image = coco.imgs[img_id]
            h, w = image['height'], image['width']

            print("Image ID ", img_id)

            persons = []
            prev_center = []

            for p in range(numPeople):

                # skip this person if parts number is too low or if
                # segmentation area is too small
                if img_anns[p]["num_keypoints"] < 5 or img_anns[p]["area"] < 32 * 32:
                    continue

                anno = img_anns[p]["keypoints"]

                pers = dict()

                person_center = [img_anns[p]["bbox"][0] + img_anns[p]["bbox"][2] / 2,
                                 img_anns[p]["bbox"][1] + img_anns[p]["bbox"][3] / 2]

                # skip this person if the distance to exiting person is too small
                flag = 0
                for pc in prev_center:
                    a = np.expand_dims(pc[:2], axis=0)
                    b = np.expand_dims(person_center, axis=0)
                    dist = cdist(a, b)[0]
                    if dist < pc[2]*0.3:
                        flag = 1
                        continue

                if flag == 1:
                    continue

                pers["objpos"] = person_center
                pers["bbox"] = img_anns[p]["bbox"]
                pers["segment_area"] = img_anns[p]["area"]
                pers["num_keypoints"] = img_anns[p]["num_keypoints"]

                pers["joint"] = np.zeros((17, 3))
                for part in range(17):
                    pers["joint"][part, 0] = anno[part * 3]
                    pers["joint"][part, 1] = anno[part * 3 + 1]

                    if anno[part * 3 + 2] == 2:
                        pers["joint"][part, 2] = 1
                    elif anno[part * 3 + 2] == 1:
                        pers["joint"][part, 2] = 0
                    else:
                        pers["joint"][part, 2] = 2

                pers["scale_provided"] = img_anns[p]["bbox"][3] / 368

                persons.append(pers)
                prev_center.append(np.append(person_center, max(img_anns[p]["bbox"][2], img_anns[p]["bbox"][3])))


            if len(persons) > 0:

                joint_all.append(dict())

                joint_all[count]["dataset"] = dataset_type

                if count < val_size:
                    isValidation = 1
                else:
                    isValidation = 0

                joint_all[count]["isValidation"] = isValidation

                joint_all[count]["img_width"] = w
                joint_all[count]["img_height"] = h
                joint_all[count]["image_id"] = img_id
                joint_all[count]["annolist_index"] = i

                # set image path
                if j is 0:
                    joint_all[count]["img_paths"] = os.path.join(
                        images_dir, 'COCO_train2014_{:012d}.jpg'.format(img_id))
                    joint_all[count]["mask_miss_paths"] = os.path.join(masks_dir,
                                                                       'mask_miss_%012d.png' % img_id)
                    joint_all[count]["mask_all_paths"] = os.path.join(masks_dir,
                                                                      'mask_all_%012d.png' % img_id)
                else:
                    joint_all[count]["img_paths"] = os.path.join(
                        images_dir, 'COCO_val2014_{:012d}.jpg'.format(img_id))
                    joint_all[count]["mask_miss_paths"] = os.path.join(masks_dir,
                                                                       'mask_miss_%012d.png' % img_id)
                    joint_all[count]["mask_all_paths"] = os.path.join(masks_dir,
                                                                      'mask_all_%012d.png' % img_id)
                    

                # set the main person
                joint_all[count]["objpos"] = persons[0]["objpos"]
                joint_all[count]["bbox"] = persons[0]["bbox"]
                joint_all[count]["segment_area"] = persons[0]["segment_area"]
                joint_all[count]["num_keypoints"] = persons[0]["num_keypoints"]
                joint_all[count]["joint_self"] = persons[0]["joint"]
                joint_all[count]["scale_provided"] = persons[0]["scale_provided"]

                # set other persons
                joint_all[count]["joint_others"] = []
                joint_all[count]["scale_provided_other"] = []
                joint_all[count]["objpos_other"] = []
                joint_all[count]["bbox_other"] = []
                joint_all[count]["segment_area_other"] = []
                joint_all[count]["num_keypoints_other"] = []

                for ot in range(1, len(persons)):
                    joint_all[count]["joint_others"].append(persons[ot]["joint"])
                    joint_all[count]["scale_provided_other"].append(persons[ot]["scale_provided"])
                    joint_all[count]["objpos_other"].append(persons[ot]["objpos"])
                    joint_all[count]["bbox_other"].append(persons[ot]["bbox"])
                    joint_all[count]["segment_area_other"].append(persons[ot]["segment_area"])
                    joint_all[count]["num_keypoints_other"].append(persons[ot]["num_keypoints"])

                joint_all[count]["people_index"] = 0
                lenOthers = len(persons) - 1

                joint_all[count]["numOtherPeople"] = lenOthers

                count += 1


def writeHDF5():

    train_hdf5 = h5py.File(train_hdf5_path, 'w')
    train_group = train_hdf5.create_group('datum')
    train_write_count = 0

    val_hdf5 = h5py.File(val_hdf5_path, 'w')
    val_group = val_hdf5.create_group('datum')
    val_write_count = 0

    data = joint_all
    numSample = len(data)

    isValidationArray = [data[i]['isValidation'] for i in range(numSample)]
    val_total_write_count = isValidationArray.count(0.0)
    tr_total_write_count = len(data) - val_total_write_count

    print("Num samples " , numSample)

    random_order = [ i for i,el in enumerate(range(len(data)))] #np.random.permutation(numSample).tolist()

    for count in range(numSample):
        idx = random_order[count]
        
        print(data[idx]['img_paths'])
        img = cv2.imread(data[idx]['img_paths'])
        mask_all = cv2.imread(data[idx]['mask_all_paths'], 0)
        mask_miss = cv2.imread(data[idx]['mask_miss_paths'], 0)

        isValidation = data[idx]['isValidation']

        height = img.shape[0]
        width = img.shape[1]
        if (width < 64):
            img = cv2.copyMakeBorder(img, 0, 0, 0, 64 - width, cv2.BORDER_CONSTANT,
                                     value=(128, 128, 128))
            print('saving padded image!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!')
            cv2.imwrite('padded_img.jpg', img)
            width = 64
        # no modify on width, because we want to keep information
        meta_data = np.zeros(shape=(height, width, 1), dtype=np.uint8)
        # print type(img), img.shape
        # print type(meta_data), meta_data.shape
        clidx = 0  # current line index
        # dataset name (string)
        for i in range(len(data[idx]['dataset'])):
            meta_data[clidx][i] = ord(data[idx]['dataset'][i])
        clidx = clidx + 1
        # image height, image width
        height_binary = float2bytes(data[idx]['img_height'])
        for i in range(len(height_binary)):
            meta_data[clidx][i] = height_binary[i]
        width_binary = float2bytes(data[idx]['img_width'])
        for i in range(len(width_binary)):
            meta_data[clidx][4 + i] = width_binary[i]
        clidx = clidx + 1
        # (a) isValidation(uint8), numOtherPeople (uint8), people_index (uint8), annolist_index (float), writeCount(float), totalWriteCount(float)
        meta_data[clidx][0] = data[idx]['isValidation']
        meta_data[clidx][1] = data[idx]['numOtherPeople']
        meta_data[clidx][2] = data[idx]['people_index']
        annolist_index_binary = float2bytes(data[idx]['annolist_index'])
        for i in range(len(annolist_index_binary)):  # 3,4,5,6
            meta_data[clidx][3 + i] = annolist_index_binary[i]
        if isValidation:
            count_binary = float2bytes(float(val_write_count))
        else:
            count_binary = float2bytes(float(train_write_count))
        for i in range(len(count_binary)):
            meta_data[clidx][7 + i] = count_binary[i]
        if isValidation:
            totalWriteCount_binary = float2bytes(float(val_total_write_count))
        else:
            totalWriteCount_binary = float2bytes(float(tr_total_write_count))
        for i in range(len(totalWriteCount_binary)):
            meta_data[clidx][11 + i] = totalWriteCount_binary[i]
        nop = int(data[idx]['numOtherPeople'])
        clidx = clidx + 1
        # (b) objpos_x (float), objpos_y (float)
        objpos_binary = float2bytes(data[idx]['objpos'])
        for i in range(len(objpos_binary)):
            meta_data[clidx][i] = objpos_binary[i]
        clidx = clidx + 1
        # (c) scale_provided (float)
        scale_provided_binary = float2bytes(data[idx]['scale_provided'])
        for i in range(len(scale_provided_binary)):
            meta_data[clidx][i] = scale_provided_binary[i]
        clidx = clidx + 1
        # (d) joint_self (3*16) (float) (3 line)
        joints = np.asarray(data[idx]['joint_self']).T.tolist()  # transpose to 3*16
        for i in range(len(joints)):
            row_binary = float2bytes(joints[i])
            for j in range(len(row_binary)):
                meta_data[clidx][j] = row_binary[j]
            clidx = clidx + 1
        # (e) check nop, prepare arrays
        if (nop != 0):
            joint_other = data[idx]['joint_others']
            objpos_other = data[idx]['objpos_other']
            scale_provided_other = data[idx]['scale_provided_other']
            # (f) objpos_other_x (float), objpos_other_y (float) (nop lines)
            for i in range(nop):
                objpos_binary = float2bytes(objpos_other[i])
                for j in range(len(objpos_binary)):
                    meta_data[clidx][j] = objpos_binary[j]
                clidx = clidx + 1
            # (g) scale_provided_other (nop floats in 1 line)
            scale_provided_other_binary = float2bytes(scale_provided_other)
            for j in range(len(scale_provided_other_binary)):
                meta_data[clidx][j] = scale_provided_other_binary[j]
            clidx = clidx + 1
            # (h) joint_others (3*16) (float) (nop*3 lines)
            for n in range(nop):
                joints = np.asarray(joint_other[n]).T.tolist()  # transpose to 3*16
                for i in range(len(joints)):
                    row_binary = float2bytes(joints[i])
                    for j in range(len(row_binary)):
                        meta_data[clidx][j] = row_binary[j]
                    clidx = clidx + 1

        # print meta_data[0:12,0:48]
        # total 7+4*nop lines
        if "COCO" in data[idx]['dataset']:
            img4ch = np.concatenate((img, meta_data, mask_miss[..., None], mask_all[..., None]),
                                    axis=2)
        elif "MPI" in data[idx]['dataset']:
            img4ch = np.concatenate((img, meta_data, mask_miss[..., None]), axis=2)

        img4ch = np.transpose(img4ch, (2, 0, 1))

        if isValidation:
            key = '%07d' % val_write_count
            val_group.create_dataset(key, data=img4ch, chunks=None)
            val_write_count += 1
        else:
            key = '%07d' % train_write_count
            train_group.create_dataset(key, data=img4ch, chunks=None)
            train_write_count += 1

        print('Writing sample %d/%d' % (count, numSample))

def float2bytes(floats):
    if type(floats) is float:
        floats = [floats]
    if type(floats) is int:
        floats = [float(floats)]

    if type(floats) is list and len(floats) > 0 and type(floats[0]) is list:
        floats = floats[0]

    return struct.pack('%sf' % len(floats), *floats)


if __name__ == '__main__':
    # Please modify input path  to locate you file
    DATASETS_ROOT_DIR = './datasets'

    # Training set
    train_annotations_path = os.path.join(
        DATASETS_ROOT_DIR, 'annotations_coco2014/person_keypoints_train2014.json')
    train_images_path = os.path.join(DATASETS_ROOT_DIR, 'train_coco2014')
    train_mask_path = os.path.join(DATASETS_ROOT_DIR, 'mask_train_coco2014')
    
    # Validation set
    val_annotations_path = os.path.join(
        DATASETS_ROOT_DIR, 'annotations_coco2014/person_keypoints_val2014.json')
    val_images_path = os.path.join(DATASETS_ROOT_DIR, 'val_coco2014')
    val_mask_path = os.path.join(DATASETS_ROOT_DIR, 'mask_val_coco2014')

    # Combianed all datasets in list
    datasets = [
        (train_annotations_path, train_images_path, train_mask_path, 'COCO'),
        (val_annotations_path, val_images_path, val_mask_path, 'COCO')
    ]
    
    # Initialle a list to store all joint
    joint_all = []
    
    # The output path
    train_hdf5_path = os.path.join(DATASETS_ROOT_DIR, 'train_dataset.h5')
    val_hdf5_path = os.path.join(DATASETS_ROOT_DIR, 'validation_dataset.h5')
    
    # Size of validation set
    val_size = 2645 
    #val_size = 300
    
    process()
    writeHDF5()

loading annotations into memory...
Done (t=3.56s)
creating index...
index created!
Image ID  57870
Image ID  384029
Image ID  222016
Image ID  520950
Image ID  69675
Image ID  547471
Image ID  122688
Image ID  392136
Image ID  398494
Image ID  90570
Image ID  504616
Image ID  161919
Image ID  457732
Image ID  44404
Image ID  4428
Image ID  170558
Image ID  405613
Image ID  283524
Image ID  37015
Image ID  71631
Image ID  491269
Image ID  365363
Image ID  64460
Image ID  581674
Image ID  470072
Image ID  344806
Image ID  84427
Image ID  317237
Image ID  409382
Image ID  570608
Image ID  469605
Image ID  356702
Image ID  405207
Image ID  472925
Image ID  214704
Image ID  279108
Image ID  438422
Image ID  257350
Image ID  393493
Image ID  62426
Image ID  19380
Image ID  485894
Image ID  446014
Image ID  530683
Image ID  292835
Image ID  262845
Image ID  299411
Image ID  42493
Image ID  239811
Image ID  2024
Image ID  95133
Image ID  287541
Image ID  441488
Image ID  179620
Image ID  70000

Image ID  333461
Image ID  579312
Image ID  176726
Image ID  5559
Image ID  448069
Image ID  395192
Image ID  118412
Image ID  210810
Image ID  102630
Image ID  170193
Image ID  204351
Image ID  368548
Image ID  48707
Image ID  63378
Image ID  58481
Image ID  492642
Image ID  475142
Image ID  408219
Image ID  120159
Image ID  248002
Image ID  340674
Image ID  490385
Image ID  439518
Image ID  27627
Image ID  403463
Image ID  77444
Image ID  51396
Image ID  147961
Image ID  343201
Image ID  320471
Image ID  370537
Image ID  380520
Image ID  343655
Image ID  230537
Image ID  339579
Image ID  223595
Image ID  498722
Image ID  471762
Image ID  277857
Image ID  465829
Image ID  282514
Image ID  29813
Image ID  405013
Image ID  4172
Image ID  491107
Image ID  246120
Image ID  577022
Image ID  147914
Image ID  81981
Image ID  540679
Image ID  23451
Image ID  254948
Image ID  441883
Image ID  476537
Image ID  390923
Image ID  460617
Image ID  80123
Image ID  117677
Image ID  481736
Image ID  5

Image ID  208196
Image ID  21504
Image ID  420412
Image ID  197257
Image ID  494217
Image ID  299413
Image ID  277072
Image ID  176321
Image ID  552569
Image ID  203843
Image ID  121599
Image ID  284756
Image ID  138435
Image ID  214250
Image ID  548118
Image ID  511781
Image ID  352841
Image ID  121232
Image ID  384099
Image ID  401721
Image ID  331139
Image ID  349144
Image ID  324334
Image ID  129310
Image ID  243836
Image ID  273336
Image ID  286525
Image ID  178770
Image ID  293374
Image ID  483781
Image ID  111727
Image ID  258362
Image ID  460094
Image ID  250196
Image ID  62395
Image ID  408465
Image ID  107013
Image ID  403394
Image ID  446935
Image ID  507370
Image ID  18820
Image ID  9174
Image ID  67405
Image ID  6489
Image ID  440087
Image ID  37183
Image ID  344477
Image ID  152693
Image ID  572152
Image ID  95337
Image ID  393896
Image ID  22056
Image ID  357656
Image ID  518257
Image ID  550021
Image ID  65252
Image ID  452861
Image ID  126907
Image ID  95363
Image ID  

Image ID  562972
Image ID  432288
Image ID  298900
Image ID  499125
Image ID  397824
Image ID  30643
Image ID  477310
Image ID  467369
Image ID  414747
Image ID  270844
Image ID  260838
Image ID  196294
Image ID  265701
Image ID  107979
Image ID  559132
Image ID  393442
Image ID  518293
Image ID  553051
Image ID  569550
Image ID  513093
Image ID  375802
Image ID  495334
Image ID  282471
Image ID  354094
Image ID  452465
Image ID  466797
Image ID  247190
Image ID  369976
Image ID  355480
Image ID  218312
Image ID  104768
Image ID  254577
Image ID  308780
Image ID  518100
Image ID  250434
Image ID  532457
Image ID  251569
Image ID  477563
Image ID  387181
Image ID  560923
Image ID  224083
Image ID  458604
Image ID  572046
Image ID  4278
Image ID  574747
Image ID  62257
Image ID  6004
Image ID  120067
Image ID  368738
Image ID  518361
Image ID  483175
Image ID  497633
Image ID  183971
Image ID  97314
Image ID  449104
Image ID  163840
Image ID  182411
Image ID  318541
Image ID  48160
Image

Image ID  105047
Image ID  375951
Image ID  455287
Image ID  450700
Image ID  549301
Image ID  503421
Image ID  7357
Image ID  276515
Image ID  369126
Image ID  121328
Image ID  379312
Image ID  136849
Image ID  333664
Image ID  523186
Image ID  406296
Image ID  163230
Image ID  390756
Image ID  227897
Image ID  191456
Image ID  395473
Image ID  114653
Image ID  403966
Image ID  347482
Image ID  75971
Image ID  398463
Image ID  98355
Image ID  296883
Image ID  556624
Image ID  322934
Image ID  541855
Image ID  170130
Image ID  538273
Image ID  337262
Image ID  6042
Image ID  542316
Image ID  232723
Image ID  468985
Image ID  399165
Image ID  55202
Image ID  467878
Image ID  171376
Image ID  44996
Image ID  476881
Image ID  522054
Image ID  51001
Image ID  157242
Image ID  155172
Image ID  530475
Image ID  240195
Image ID  409706
Image ID  546148
Image ID  581204
Image ID  475313
Image ID  138367
Image ID  92054
Image ID  493822
Image ID  361469
Image ID  327970
Image ID  355022
Image I

...

Writing sample 54779/55242
./datasets/val_coco2014/COCO_val2014_000000266847.jpg
Writing sample 54780/55242
./datasets/val_coco2014/COCO_val2014_000000358019.jpg
Writing sample 54781/55242
./datasets/val_coco2014/COCO_val2014_000000541744.jpg
Writing sample 54782/55242
./datasets/val_coco2014/COCO_val2014_000000277642.jpg
Writing sample 54783/55242
./datasets/val_coco2014/COCO_val2014_000000040886.jpg
Writing sample 54784/55242
./datasets/val_coco2014/COCO_val2014_000000157928.jpg
Writing sample 54785/55242
./datasets/val_coco2014/COCO_val2014_000000043657.jpg
Writing sample 54786/55242
./datasets/val_coco2014/COCO_val2014_000000259755.jpg
Writing sample 54787/55242
./datasets/val_coco2014/COCO_val2014_000000342403.jpg
Writing sample 54788/55242
./datasets/val_coco2014/COCO_val2014_000000558457.jpg
Writing sample 54789/55242
./datasets/val_coco2014/COCO_val2014_000000491921.jpg
Writing sample 54790/55242
./datasets/val_coco2014/COCO_val2014_000000410019.jpg
Writing sample 54791/55242
.

Writing sample 54893/55242
./datasets/val_coco2014/COCO_val2014_000000388215.jpg
Writing sample 54894/55242
./datasets/val_coco2014/COCO_val2014_000000351588.jpg
Writing sample 54895/55242
./datasets/val_coco2014/COCO_val2014_000000332627.jpg
Writing sample 54896/55242
./datasets/val_coco2014/COCO_val2014_000000551995.jpg
Writing sample 54897/55242
./datasets/val_coco2014/COCO_val2014_000000111609.jpg
Writing sample 54898/55242
./datasets/val_coco2014/COCO_val2014_000000473370.jpg
Writing sample 54899/55242
./datasets/val_coco2014/COCO_val2014_000000174888.jpg
Writing sample 54900/55242
./datasets/val_coco2014/COCO_val2014_000000544695.jpg
Writing sample 54901/55242
./datasets/val_coco2014/COCO_val2014_000000224702.jpg
Writing sample 54902/55242
./datasets/val_coco2014/COCO_val2014_000000431738.jpg
Writing sample 54903/55242
./datasets/val_coco2014/COCO_val2014_000000404145.jpg
Writing sample 54904/55242
./datasets/val_coco2014/COCO_val2014_000000064718.jpg
Writing sample 54905/55242
.

Writing sample 55008/55242
./datasets/val_coco2014/COCO_val2014_000000116133.jpg
Writing sample 55009/55242
./datasets/val_coco2014/COCO_val2014_000000157581.jpg
Writing sample 55010/55242
./datasets/val_coco2014/COCO_val2014_000000416523.jpg
Writing sample 55011/55242
./datasets/val_coco2014/COCO_val2014_000000291202.jpg
Writing sample 55012/55242
./datasets/val_coco2014/COCO_val2014_000000359451.jpg
Writing sample 55013/55242
./datasets/val_coco2014/COCO_val2014_000000119709.jpg
Writing sample 55014/55242
./datasets/val_coco2014/COCO_val2014_000000151988.jpg
Writing sample 55015/55242
./datasets/val_coco2014/COCO_val2014_000000270744.jpg
Writing sample 55016/55242
./datasets/val_coco2014/COCO_val2014_000000529159.jpg
Writing sample 55017/55242
./datasets/val_coco2014/COCO_val2014_000000054679.jpg
Writing sample 55018/55242
./datasets/val_coco2014/COCO_val2014_000000283768.jpg
Writing sample 55019/55242
./datasets/val_coco2014/COCO_val2014_000000561187.jpg
Writing sample 55020/55242
.

Writing sample 55117/55242
./datasets/val_coco2014/COCO_val2014_000000165353.jpg
Writing sample 55118/55242
./datasets/val_coco2014/COCO_val2014_000000126434.jpg
Writing sample 55119/55242
./datasets/val_coco2014/COCO_val2014_000000279407.jpg
Writing sample 55120/55242
./datasets/val_coco2014/COCO_val2014_000000413124.jpg
Writing sample 55121/55242
./datasets/val_coco2014/COCO_val2014_000000142698.jpg
Writing sample 55122/55242
./datasets/val_coco2014/COCO_val2014_000000520528.jpg
Writing sample 55123/55242
./datasets/val_coco2014/COCO_val2014_000000236432.jpg
Writing sample 55124/55242
./datasets/val_coco2014/COCO_val2014_000000236874.jpg
Writing sample 55125/55242
./datasets/val_coco2014/COCO_val2014_000000281829.jpg
Writing sample 55126/55242
./datasets/val_coco2014/COCO_val2014_000000000474.jpg
Writing sample 55127/55242
./datasets/val_coco2014/COCO_val2014_000000553788.jpg
Writing sample 55128/55242
./datasets/val_coco2014/COCO_val2014_000000113233.jpg
Writing sample 55129/55242
.

Writing sample 55229/55242
./datasets/val_coco2014/COCO_val2014_000000394940.jpg
Writing sample 55230/55242
./datasets/val_coco2014/COCO_val2014_000000037728.jpg
Writing sample 55231/55242
./datasets/val_coco2014/COCO_val2014_000000001404.jpg
Writing sample 55232/55242
./datasets/val_coco2014/COCO_val2014_000000296759.jpg
Writing sample 55233/55242
./datasets/val_coco2014/COCO_val2014_000000227204.jpg
Writing sample 55234/55242
./datasets/val_coco2014/COCO_val2014_000000138075.jpg
Writing sample 55235/55242
./datasets/val_coco2014/COCO_val2014_000000561160.jpg
Writing sample 55236/55242
./datasets/val_coco2014/COCO_val2014_000000215244.jpg
Writing sample 55237/55242
./datasets/val_coco2014/COCO_val2014_000000015335.jpg
Writing sample 55238/55242
./datasets/val_coco2014/COCO_val2014_000000572233.jpg
Writing sample 55239/55242
./datasets/val_coco2014/COCO_val2014_000000560744.jpg
Writing sample 55240/55242
./datasets/val_coco2014/COCO_val2014_000000074478.jpg
Writing sample 55241/55242
